In [1]:
import json
import datetime
import numpy as np
import pandas as pd
import altair as alt
import matplotlib.pyplot as plt
from collections import defaultdict
from sklearn.linear_model import LinearRegression

In [2]:
trends = pd.read_csv('google_trend_sp500.csv')
earnings = pd.read_csv('earnings_latest.csv')

In [2]:
'''
The below file, while not mentioned in the report, 
can be obtained from the same data source as the earnings_latest file. 
It was added into the data in the hopes of being investigated in the future.

The file can be downloaded at the following URL:
https://www.kaggle.com/tsaustin/us-historical-stock-prices-with-earnings-data

NOTE: stock_prices_latest.csv is a 2GB file so we want to pare it down immediately
'''
stocks = pd.read_csv('stock_prices_latest.csv')

'\nThe below file, while not mentioned in the report, \ncan be obtained from the same data source as the earnings_latest file. \nIt was added into the data in the hopes of being investigated in the future.\n\nThe file can be downloaded at the following URL:\nhttps://www.kaggle.com/tsaustin/us-historical-stock-prices-with-earnings-data\n\nNOTE: stock_prices_latest.csv is a 2GB file so we want to pare it down immediately\n'

In [3]:
sp500_companies = trends.columns.to_list()
stock_mask = stocks.symbol.isin(sp500_companies)
stocks = stocks[stock_mask]

In [4]:
trends['date'] = pd.to_datetime(trends['date'])
stocks['date'] = pd.to_datetime(stocks['date'])
trends.head()

date  MMM  AOS  ABT  ABBV  ABMD  ACN  ATVI  ADBE  AAP  ...  WLTW  \
0 2016-05-22   10   37    6     4     0   21     7     6    5  ...     0   
1 2016-05-29    2    0    2     8    16   11     8     4   23  ...    24   
2 2016-06-05   16   19    6    21     0   19     5     8   14  ...     0   
3 2016-06-12    6   19    3     4     8   13     5     8    4  ...     0   
4 2016-06-19    7    0    5    12     0   22     9    26   14  ...     0   

   WYNN  XEL  XLNX  XYL  YUM  ZBRA  ZBH  ZION  ZTS  
0     5   15     9   23   13     0   13     0    0  
1     8   31     3    0    9     0    0     3   29  
2     4    0     0    0   25     0   38     0   29  
3     6   45     0    0   24     0   13     1   29  
4     4   15     3    0   11    11   13     1   29  

[5 rows x 506 columns]

In [5]:
stocks.head()

symbol       date   open   high    low  close  close_adjusted     volume  \
0   MSFT 2016-05-16  50.80  51.96  50.75  51.83         49.7013   20032017   
1   MSFT 2002-01-16  68.85  69.84  67.85  67.87         22.5902   30977700   
2   MSFT 2001-09-18  53.41  55.00  53.17  54.32         18.0802   41591300   
3   MSFT 2007-10-26  36.01  36.03  34.56  35.03         27.2232  288121200   
4   MSFT 2014-06-27  41.61  42.29  41.51  42.25         38.6773   74640000   

   split_coefficient  
0                1.0  
1                1.0  
2                1.0  
3                1.0  
4                1.0

In [6]:
def create_stockprice_trend(symbols, stocks):
    _monthly_trends = pd.DataFrame(columns=['symbol', 'date', 'stock_slope'])
    for symbol in symbols:
        try:
            ticker_stock = stocks[stocks.symbol == symbol]
            ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)

            close_price = ticker_stock.groupby('month')['close'].apply(list).tolist()
            dates = ticker_stock.groupby('month')['date'].apply(list).tolist()
            for x,y in zip(dates, close_price):
                X = [[int(i.strftime('%s'))] for i in x]
                model = LinearRegression().fit(X,y)
                new_entry = {
                    'symbol': symbol,
                    'date': datetime.date(x[0].year, x[0].month, 1),
                    'stock_slope': model.coef_[0],
                }
                _monthly_trends = _monthly_trends.append(new_entry, ignore_index=True)
        except:
            print(symbol)
    return _monthly_trends



In [7]:
stock_sloped = create_stockprice_trend(sp500_companies, stocks)
stock_sloped['date'] = pd.to_datetime(stock_sloped['date'])

date


<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)
<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)
<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value inst

<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)
<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)
<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value inst

<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)
<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)
<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value inst

BKR


...

<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)
<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)
<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value inst

<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)
<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)
<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value inst

VTRS


<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)
<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)
<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value inst

<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)
<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_stock['month'] = ticker_stock.apply(lambda x: x.date.strftime('%m/%Y'), axis=1)
<ipython-input-6-d3b187b151d4>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value inst

### Formatting Earnings and Preliminary Work
Working to ensure that the `earning_latest.csv` data is properly formatted and free of NaNs. Additionally, creating a mapper that will make dates to fiscal quarters, and quarter month ranges to fiscal quarters.

In [9]:
sp500_companies = trends.columns.to_list()
sp500_companies.remove('date')
# Filter earnings to only the companies in our trends data
sp500_earnings_mask = earnings.symbol.isin(sp500_companies)
earnings = earnings[sp500_earnings_mask]

# Filter out NaN within eps and eps_est
earnings = earnings[earnings['eps'].notna()]
earnings = earnings[earnings['eps_est'].notna()]
earnings = earnings[earnings['qtr'].notna()]

earnings.head()

symbol        date      qtr  eps_est   eps release_time
14      A  2012-11-19  10/2012     0.80  0.84         post
15      A  2013-02-14  01/2013     0.66  0.63         post
16      A  2013-05-14  04/2013     0.67  0.77         post
17      A  2013-08-14  07/2013     0.62  0.68         post
18      A  2013-11-14  10/2013     0.76  0.81         post

In [10]:
def generate_month_range(start, end):
    _range = np.arange(start, (end+1))
    # if arange doesn't create an array intervene
    if (len(_range) == 0):
        _range = [start%13, (start+1)%13, (start+2)%13]
        _range = [r + 1 if (r < 10) else r for r in _range]
    
    return _range
    
def build_quarter_mapping(symbols, earning):
    '''
    Given a list of stock symbols and earnings DF,
    create a mapping of dates to fiscal quarters
    '''
    mapping = {}
    for symbol in symbols:
        subset_df = earning[earning.symbol == symbol]
        potential_dates = subset_df.qtr.unique()

        filtered_months = [dt.split('/')[0] for dt in potential_dates if 'Q' not in dt]
        unique_months = set(filtered_months)
        ordered_months = sorted(list(unique_months))
        
        # ensure we have 4 dates corresponding to quarters
        if (len(ordered_months) == 4):
            mapping[symbol] = {}
            mapped_months = {}
            mapped_months['Q1'] = ordered_months[0]
            mapped_months['Q2'] = ordered_months[1]
            mapped_months['Q3'] = ordered_months[2]
            mapped_months['Q4'] = ordered_months[3]
            mapping[symbol]['quarters'] = mapped_months
            
            mapped_ranges = {}
            mapped_ranges['Q1'] = generate_month_range(int(ordered_months[3]) + 1,int(ordered_months[0]))
            mapped_ranges['Q2'] = generate_month_range(int(ordered_months[0]) + 1,int(ordered_months[1]))
            mapped_ranges['Q3'] = generate_month_range(int(ordered_months[1]) + 1,int(ordered_months[2]))
            mapped_ranges['Q4'] = generate_month_range(int(ordered_months[2]) + 1,int(ordered_months[3]))
            
            mapping[symbol]['ranges'] = mapped_ranges 
            
    return mapping
        

In [11]:
quarter_mappings = build_quarter_mapping(sp500_companies, earnings)

In [12]:
# Identify which companies are not in both datasets
omitted_from_mapping = [i for i in sp500_companies if i not in quarter_mappings.keys()]
print(omitted_from_mapping)

['AMCR', 'BKR', 'CARR', 'CTVA', 'DFS', 'DOW', 'DD', 'EVRG', 'GPN', 'GL', 'PEAK', 'HWM', 'J', 'LHX', 'LDOS', 'LUMN', 'NLOK', 'OTIS', 'RTX', 'MOS', 'TT', 'TFC', 'VIAC', 'VTRS']


In [13]:
mapping_mask = earnings.symbol.isin(omitted_from_mapping)
earnings = earnings[~mapping_mask]
trends.drop(omitted_from_mapping, axis=1, inplace=True)

In [14]:
def encode_reported_earnings(row):
    if (row.eps > row.eps_est):
        return 1
    elif (row.eps < row.eps_est):
        return -1
    else:
        return 0
    
earnings['result'] = earnings.apply(encode_reported_earnings, axis=1)
earnings.head()

symbol        date      qtr  eps_est   eps release_time  result
14      A  2012-11-19  10/2012     0.80  0.84         post       1
15      A  2013-02-14  01/2013     0.66  0.63         post      -1
16      A  2013-05-14  04/2013     0.67  0.77         post       1
17      A  2013-08-14  07/2013     0.62  0.68         post       1
18      A  2013-11-14  10/2013     0.76  0.81         post       1

In [15]:
quarter_mappings['A']

{'quarters': {'Q1': '01', 'Q2': '04', 'Q3': '07', 'Q4': '10'},
 'ranges': {'Q1': [11, 12, 1],
  'Q2': array([2, 3, 4]),
  'Q3': array([5, 6, 7]),
  'Q4': array([ 8,  9, 10])}}

### Merging Datasets
The goal of merging it to create a DataFrame where for each row we have the independent and dependent variables in a single row - for a single stock symbol.

The end column schema will be `ticker symbol, Mo. 1 Avg. Search Vol (M1ASV), M2ASV, M3ASV, Results`

In [16]:
def compress_date(row):
    return row.date.strftime('%m/%Y')
trends['compressed_date'] = trends.apply(compress_date, axis=1)

In [17]:
trends = trends.groupby('compressed_date').mean().reset_index()
trends['compressed_date'] = pd.to_datetime(trends['compressed_date'])
trends.iloc[0]

compressed_date    2017-01-01 00:00:00
MMM                                7.8
AOS                               10.4
ABT                                5.4
ABBV                              17.8
                          ...         
YUM                               25.0
ZBRA                               1.8
ZBH                               23.4
ZION                               4.4
ZTS                                2.6
Name: 0, Length: 482, dtype: object

In [18]:
quarters = ['Q1', 'Q2', 'Q3', 'Q4']
def get_quarter(dt, symbol, mapper):
    month = dt.month
    for quarter in quarters:
        _range = mapper[symbol]['ranges'][quarter]
        if (month in _range):
            return quarter
    
def reform_trends(symbols, trends, mapper):
    reformed_df = pd.DataFrame(columns=['symbol', 'date', 'asv', 'quarter', 'year'])
    for symbol in symbols:
        subset_trends = trends[['compressed_date', symbol]]
        for index, row in subset_trends.iterrows():
            new_row = {
                'symbol': symbol,
                'date': row.compressed_date,
                'asv': row[symbol],
                'quarter': get_quarter(row.compressed_date, symbol, mapper),
                'year': row.compressed_date.year,
            }
            reformed_df = reformed_df.append(new_row, ignore_index=True)
    return reformed_df

def compress_quarterly_annual_trend(qat):
    _vals = []
    _dates = []
    if len(qat) == 3:
        for index, row in qat.iterrows():
            _vals.append(row.asv)
            _dates.append(row.date)
        entry = {
            'symbol': qat.iloc[0].symbol,
            'asv1': _vals[0],
            'date1': _dates[0],
            'asv2': _vals[1],
            'date2': _dates[1],
            'asv3': _vals[2],
            'date3': _dates[2],
            'quarter': qat.iloc[0].quarter,
            'year_end': qat.iloc[-1].year,
        }
        return entry
    else:
        pass

def consolidate_trends(symbols, trend, mapper):
    nov_start_rollover = [11, 12, 1]
    dec_start_rollover = [12, 1, 2]
    consolidated_df = pd.DataFrame(columns=['symbol', 'asv1', 'asv2', 'asv3', 'date1', 'date2', 'date3', 'quarter', 'year_end'])
    reformed_df = reform_trends(symbols, trend, mapper)
    for symbol in symbols:
        sym_trend = reformed_df[reformed_df.symbol == symbol]
        sym_trend['date'] = pd.to_datetime(sym_trend['date'])
        years = sym_trend.year.unique()
        for year in years:
            for quarter in quarters:
                annual_quarterly_trend = sym_trend[
                    (sym_trend.year == year) & (sym_trend.quarter == quarter)
                ].sort_values('date')
                if (quarter == 'Q1'):
                    _loc_months = [i.month for i in annual_quarterly_trend.date]
                    if any(_mon in [1,2] for _mon in _loc_months):
                        if all(i in nov_start_rollover for i in _loc_months):
                            _tmp_df = pd.DataFrame(columns=[])
                            for dt in nov_start_rollover:
                                if (dt == 1):
                                    _tmp_dt = datetime.date(year, dt, 1).strftime('%Y-%m-%d')
                                else:
                                    _tmp_dt = datetime.date((year-1), dt, 1).strftime('%Y-%m-%d')
                                _tmp_df = _tmp_df.append(
                                    sym_trend[sym_trend.date.dt.date.astype(str) == _tmp_dt]
                                )
                            
                            annual_quarterly_trend = _tmp_df
                consolidated_df = consolidated_df.append(compress_quarterly_annual_trend(annual_quarterly_trend), ignore_index=True)
    return consolidated_df
                        #elif (_loc_months == dec_start_rollover):
#                     if(annual_quarterly_trend.date.month in [1, 2]):
#                         print(annual_quarterly_trend.sort_values('date'))

In [19]:
revised_companies = trends.columns.to_list()
revised_companies.remove('compressed_date')
_consolidated = consolidate_trends(revised_companies, trends, quarter_mappings)
_consolidated['qtr'] = _consolidated.apply(lambda x: x.date3.strftime('%m/%Y'), axis=1)

<ipython-input-18-db70890e606d>:53: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sym_trend['date'] = pd.to_datetime(sym_trend['date'])


In [20]:
merged = _consolidated.merge(earnings, how='inner', left_on=['qtr', 'symbol'], right_on=['qtr', 'symbol'])

In [66]:
# merge date1 and reformat
merged_stock = merged.merge(stock_sloped, how='inner', left_on=['date1', 'symbol'], right_on=['date', 'symbol'])
merged_stock.drop('date_x', axis=1, inplace=True)
merged_stock.drop('date_y', axis=1, inplace=True)
merged_stock.rename(columns={'stock_slope': 'slope1',}, inplace=True)
# merge date2 and reformat
merged_stock = merged_stock.merge(stock_sloped, how='inner', left_on=['date2', 'symbol'], right_on=['date', 'symbol'])
merged_stock.drop('date', axis=1, inplace=True)
merged_stock.rename(columns={'stock_slope': 'slope2',}, inplace=True)
# merge date3 and reformat
merged_stock = merged_stock.merge(stock_sloped, how='inner', left_on=['date3', 'symbol'], right_on=['date', 'symbol'])
merged_stock.drop('date', axis=1, inplace=True)
merged_stock.rename(columns={'stock_slope': 'slope3',}, inplace=True)

In [67]:
merged_stock.head()

symbol  asv1   asv2  asv3      date1      date2      date3 quarter year_end  \
0    MMM   7.8  12.50  12.5 2017-01-01 2017-02-01 2017-03-01      Q1     2017   
1    MMM  10.8  11.50  16.0 2017-04-01 2017-05-01 2017-06-01      Q2     2017   
2    MMM  11.8   9.75  13.0 2017-07-01 2017-08-01 2017-09-01      Q3     2017   
3    MMM  17.8  15.00  17.4 2017-10-01 2017-11-01 2017-12-01      Q4     2017   
4    MMM  23.5  27.00  20.5 2018-01-01 2018-02-01 2018-03-01      Q1     2018   

       qtr  eps_est   eps release_time  result        slope1        slope2  \
0  03/2017     2.07  2.16          pre       1 -7.464901e-07  6.175366e-06   
1  06/2017     2.59  2.58          pre      -1  2.614071e-06  1.535283e-06   
2  09/2017     2.21  2.33          pre       1 -4.284754e-06 -1.517089e-06   
3  12/2017     2.03  2.10          pre       1  8.358566e-06  2.990876e-06   
4  03/2018     2.50  2.50          pre       0  7.104077e-06  9.227658e-07   

         slope3  
0  8.487097e-07  
1  2.534501e-06  
2  3.408106e-06  
3 -2.043193e-06  
4 -7.456956e-06

In [68]:
merged_stock.to_csv('merged_datasets.csv')
tmp = merged_stock.copy(deep=True)
tmp['asv_avg'] = tmp.apply(lambda x: np.mean([x.asv1, x.asv2, x.asv3]), axis=1)
tmp['slope_avg'] = tmp.apply(lambda x: np.mean([x.slope1, x.slope2, x.slope3]), axis=1)

In [69]:
alt.data_transformers.disable_max_rows()
trend = alt.Chart(tmp).mark_point().encode(
    x='asv_avg',
    y='slope_avg',
    color='result:N'
)
price = alt.Chart(merged_stock[merged_stock.symbol == 'MMM']).mark_point().encode(
    x='slope2',
    y='slope3',
    color='result:N'
)
trend

alt.Chart(...)

In [70]:
X = merged_stock[['slope1', 'slope2', 'slope3']]
print(X)
#model = LinearRegression().fit(,merged_stock['result'])

            slope1        slope2        slope3
0    -7.464901e-07  6.175366e-06  8.487097e-07
1     2.614071e-06  1.535283e-06  2.534501e-06
2    -4.284754e-06 -1.517089e-06  3.408106e-06
3     8.358566e-06  2.990876e-06 -2.043193e-06
4     7.104077e-06  9.227658e-07 -7.456956e-06
...            ...           ...           ...
5430 -5.382540e-07 -5.386668e-07  7.498240e-07
5431 -6.267833e-08  4.225862e-06  2.481178e-06
5432 -2.117872e-07 -2.498040e-07  3.130993e-06
5433  1.233797e-06  2.145006e-08  1.702385e-07
5434 -1.564751e-06  3.216587e-07  1.802781e-06

[5435 rows x 3 columns]


In [23]:
import matplotlib.pyplot as plt

In [71]:
alt.data_transformers.disable_max_rows()
chart11 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv1', y='asv1', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart12 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv1', y='asv2', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart13 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv1', y='asv3', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart31 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv3', y='asv1', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart32 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv3', y='asv2', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart33 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv3', y='asv3', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart21 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv2', y='asv1', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart22 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv2', y='asv2', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart23 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv2', y='asv3', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

# (chart11 | chart12 | chart13) & (chart21 | chart22 | chart23) & (chart31 | chart32 | chart33)
chart12 | chart13 | chart23

alt.HConcatChart(...)

In [76]:
popular_comp = ['AMZN', 'FB', 'GOOG', 'GOOGL', 'TSLA', 'MSFT', 'AAPL', 'JNJ']
pop_stock = merged_stock.symbol.isin(popular_comp)
merged_stock = merged_stock[pop_stock]

In [77]:
alt.data_transformers.disable_max_rows()
chart11 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv1', y='asv1', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart12 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv1', y='asv2', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart13 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv1', y='asv3', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart31 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv3', y='asv1', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart32 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv3', y='asv2', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart33 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv3', y='asv3', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart21 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv2', y='asv1', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart22 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv2', y='asv2', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

chart23 = alt.Chart(merged_stock
).mark_circle(
).encode(x='asv2', y='asv3', color=alt.Color('result:N', scale=alt.Scale(scheme='sinebow'))
).properties(
    height=200,
    width=200
)

(chart11 | chart12 | chart13) & (chart21 | chart22 | chart23) & (chart31 | chart32 | chart33)

alt.VConcatChart(...)

In [78]:
chart12 | chart13 | chart23

alt.HConcatChart(...)

In [74]:
alt.Chart(merged_stock
).mark_circle(
).encode(x='asv1', y='eps', color='result:N')

alt.Chart(...)